# Visualization showing the GISS Global Temperature anomoly distribution over time

This notebook was used to generate the visualizations released as [SVS #5065](https://svs.gsfc.nasa.gov/5065) for the NASA's Scientific Visualization Studio. Designed to be an updated version as [SVS #4891](https://svs.gsfc.nasa.gov/4981) which was inspired by an earlier SVS visualization from 2012: [SVS #3975](https://svs.gsfc.nasa.gov/3975)

The visualization illustrated how the distributions of temperatures has changed over time. We use a Kernal Density Estimator(KDE) to estimate the distribution.

[Mark SubbaRao](https://science.gsfc.nasa.gov/sed/bio/mark.u.subbarao)

In [1]:
#imports
import netCDF4 as nc
import numpy as np
from scipy.stats.kde import gaussian_kde
from scipy.stats import norm
import matplotlib
import matplotlib.pyplot as plt
import gzip
import requests

### Data Acquisition
The Data will be imported from the Goddard Institute of Space Studies here: https://data.giss.nasa.gov/gistemp/

Gridded Monthly Temperature Anomaly Data
Users interested in the entire gridded surface air temperature anomaly data may download netCDF files containing selected series on a regular 2°×2° grid or the basic SBBX binary files.

Compressed NetCDF Files (regular 2°×2° grid)
Surface air temperature (no ocean data), 250km smoothing (9 MB)

In [2]:
# Download the gzipped datafile from GISS and load it into a netCDF Dataset
GISTEMPfile = requests.get('https://data.giss.nasa.gov/pub/gistemp/gistemp250_GHCNv4.nc.gz')
ds = nc.Dataset("dummy_path", mode="r", memory=gzip.decompress(GISTEMPfile.content))
v = ds.variables['tempanomaly']

### Save This image to disk!
#### We will use it to as the colormap for the visualizations
We will be using the embedded image below as our colormap. Same this image to disk as as ***gistemp_cmap.png***




In [3]:
# Make the colormap from the saved image
from matplotlib.image import imread
from matplotlib.colors import LinearSegmentedColormap

img = imread('gistemp_cmap.png')
# just pick one column for the colormap
colors_from_img = img[3, :, :]
giss_cmap = LinearSegmentedColormap.from_list('giss_cmap', colors_from_img, N=254)

In [4]:
v

<class 'netCDF4._netCDF4.Variable'>
int16 tempanomaly(time, lat, lon)
    long_name: Surface temperature anomaly
    units: K
    scale_factor: 0.01
    cell_methods: time: mean
    _FillValue: 32767
unlimited dimensions: 
current shape = (1720, 90, 180)
filling on

## Make the Animated Graph

The animated graph will morph between the calculated temperature anomaly distributions for each year. The distribution will be filled under the curve using the color map we created above. The graph is designed to go from the years 1962-2022 with trails left behing for every 20 year increment. Some additional labelling for the final released visualization was composited in.

In [5]:
# This code block calculates the distributions that will be used to make the animation
# 
tOffset = 82 # The number of years to skip since the data started in 1880, a value of 82 starts us in 1962
timeStep = 1 # The step between calculated distributions in years
timeBins= 1 # The amount of data to bin in years, usually the same as timeStep
plotRange = (-5.,5.) # The range, in degrees Celcius, over which the PDFs will be calculates
PDFs=[]
startDates=[]
xx = np.linspace(plotRange[0],plotRange[1], 2048)
def makePDFs(latmin=-90.,latmax=90.):
    nTimeSteps = int ((v.shape[0] - 12 * tOffset) /(12 * timeStep))
    # The 2x2 degree patches cover different areas, here we create the weights to account for that
    lats = ds.variables['lat'][:].data
    #lats[lats < latmin] = 90.;
    #lats[lats > latmax] = 90.;
    lat_weights = np.broadcast_to(np.cos(np.deg2rad(lats)).reshape(1,-1,1), v.shape)
    masked_lat_weights = np.ma.array(data=lat_weights, mask=v[:].mask)
    for i in range(nTimeSteps):        
        indexMin = 12*(i*timeStep+tOffset)
        indexMax = 12*(i*timeStep+timeBins+tOffset)
        pdf = gaussian_kde(v[indexMin:indexMax,:,:].compressed(),
                           weights=masked_lat_weights[indexMin:indexMax,:,:].compressed())
        PDFs.append(pdf(xx))
        startDates.append(1880 + indexMin/12.)
    PDFs.append(pdf(xx)) #One extra to hold last position
    startDates.append(1880 + indexMin/12.)

In [6]:
makePDFs()

In [7]:
# Set the resolution for the outputs
resolutionDict = {"HD": 120, "4k": 240, "8k": 480, "print": 64, "thm": 20}
resKey = '4k'
# Find largest distribution value
#np.max(PDFs)

In [44]:
# the code to create individual frames of the visualization
def GISSfig(plotTime, startDates, PDFs, timeStep=1., ymax = 0.6, metric = True):
    from matplotlib.ticker import StrMethodFormatter
    plt.style.use('dark_background')
    fig= plt.figure (figsize=(16,9), dpi = resolutionDict[resKey])
    f,ax=plt.subplots(figsize=(16,9), dpi = resolutionDict[resKey])
    nPlot = int((plotTime-startDates[0])/timeStep)
    interpFrac = (plotTime-startDates[0])%timeStep
    plot=PDFs[nPlot]*(1-interpFrac) + interpFrac*PDFs[nPlot+1]
    res = giss_cmap((xx+2.)/4.) #This colormap is applied from -2 to 2 degrees in SVS visualizations
    for j in range(len(xx)-1):
        plt.fill_between(xx[j:j+2], np.zeros(2), plot[j:j+2], zorder=2, color=res[j])
    plt.plot(xx,plot,color='w',zorder=4)
    # leave trails
    for ghostYr in range(0,60,20):
        if (ghostYr<(nPlot+1)):
            plt.plot(xx,PDFs[ghostYr],color="grey",zorder=3)
    plt.ylim(0,ymax)
    plt.xlim(-5,5)
    plt.yticks(ticks=None)
    ax.yaxis.set_visible(False)
    if metric:
        ax.set_xticks([-4,-2,0.,2,4])     
        ax.set_xticklabels(['-4', '-2','0',  '+2', '+4'])
    else:
        ax.set_xticks([-8.*(5./9.),-6.*(5./9.),-4.*(5./9.),-2.*(5./9.),0.,2.*(5./9.),4.*(5./9.),6.*(5./9.),8.*(5./9.)])
        ax.set_xticklabels(['-8','-6','-4', '-2','0',  '+2', '+4', '+6', '+8'])
    plt.grid(True)
    plt.title("Land Temperature Anomaly Distribution",fontsize=32)
    plt.text(.78, 0.85 , f'{int(plotTime)}', fontsize=24,horizontalalignment='center', verticalalignment='center', transform=ax.transAxes)
    if metric:
        plt.xlabel(u'Temperature Anomaly (°C)', fontsize=14)
    else:
        plt.xlabel(u'Temperature Anomaly (°F)', fontsize=14)
    plt.gca().spines['left'].set_visible(False)
    plt.gca().spines['right'].set_visible(False)
    plt.gca().spines['top'].set_visible(False)


In [45]:
# This code block generates the full animation 
nStartHold = 1 # Use a value larger than one to hold on the last frame
nEndHold = 1 # Use a value larger than one to hold on the last frame in the animation
nAnimationFrames = 850 # Number of frames in the animation excluding holds
nRepeat = np.ones(nAnimationFrames)
nRepeat[0] = nStartHold
nRepeat[-1] = nEndHold
figTimes = np.linspace(1962, 2022.99, nAnimationFrames)
nFrame = 0
for i, time in enumerate(figTimes):
    GISSfig(time, startDates, PDFs, metric=False)
    for n in range(int(nRepeat[i])):
        plt.savefig("frames_2022_F/GISSTempDist_2022_%03d.png" % (nFrame), dpi = resolutionDict[resKey])
        plt.close()
        nFrame = nFrame + 1

<ipython-input-44-0d9fee1b8f33>:6: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  f,ax=plt.subplots(figsize=(16,9), dpi = resolutionDict[resKey])
<ipython-input-44-0d9fee1b8f33>:5: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  fig= plt.figure (figsize=(16,9), dpi = resolutionDict[resKey])


<Figure size 3840x2160 with 0 Axes>

<Figure size 3840x2160 with 0 Axes>

<Figure size 3840x2160 with 0 Axes>

<Figure size 3840x2160 with 0 Axes>

...

<Figure size 3840x2160 with 0 Axes>

<Figure size 3840x2160 with 0 Axes>

<Figure size 3840x2160 with 0 Axes>

<Figure size 3840x2160 with 0 Axes>

<Figure size 3840x2160 with 0 Axes>